In [82]:

import tensorflow as tf
import numpy as np
from tensorflow.keras.layers import LSTM, Activation, Dropout, Dense, Input, Conv1D, MaxPooling1D, GlobalMaxPooling1D
from tensorflow.keras.models import Model
import string
import re
from tensorflow.keras.preprocessing.text import Tokenizer
from sklearn.preprocessing import LabelBinarizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
import tensorflow.keras
from sklearn.model_selection import train_test_split
     

In [83]:
data = pd.read_csv("contracts.csv")
data.dropna(inplace = True)
data.reset_index(inplace = True,drop = True)
data

opcode       vulnerability
0    PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x32 PUSH1 ...  Overflow-Underflow
1    PUSH1 0x55 PUSH1 0x23 PUSH1 0xB DUP3 DUP3 DUP3...  Overflow-Underflow
2    PUSH1 0x80 PUSH1 0x40 MSTORE CALLVALUE DUP1 IS...  Overflow-Underflow
3    PUSH1 0x80 PUSH1 0x40 MSTORE CALLVALUE DUP1 IS...  Overflow-Underflow
4    PUSH1 0x4C PUSH1 0x2C PUSH1 0xB DUP3 DUP3 DUP3...  Overflow-Underflow
..                                                 ...                 ...
744  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 PUSH1 0...                 TOD
745  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 DUP1 PU...                 TOD
746  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 DUP1 PU...                 TOD
747  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 PUSH1 0...                 TOD
748  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 DUP1 PU...                 TOD

[749 rows x 2 columns]

In [84]:
def find_length(row):
    return len(row.opcode.split())

In [85]:
maxLen = print(data.apply(lambda a:find_length(a),axis = 1).max())
minLen = print(data.apply(lambda a:find_length(a),axis = 1).min())

29527
57


In [86]:
reloaded_word_vectors = KeyedVectors.load('vectors.kv')
reloaded_word_vectors

In [87]:
for index, word in enumerate(reloaded_word_vectors.index_to_key):
    print(f"word #{index}/{len(reloaded_word_vectors.index_to_key)} is {word}")

word #0/141 is HEX
word #1/141 is PUSH1
word #2/141 is SWAP1
word #3/141 is POP
word #4/141 is DUP1
word #5/141 is PUSH2
word #6/141 is DUP2
word #7/141 is ADD
word #8/141 is JUMPDEST
word #9/141 is AND
word #10/141 is ISZERO
word #11/141 is PUSH20
word #12/141 is MSTORE
word #13/141 is SWAP2
word #14/141 is JUMPI
word #15/141 is MLOAD
word #16/141 is JUMP
word #17/141 is DUP3
word #18/141 is SLOAD
word #19/141 is SUB
word #20/141 is DUP4
word #21/141 is REVERT
word #22/141 is PUSH4
word #23/141 is EQ
word #24/141 is KECCAK256
word #25/141 is MUL
word #26/141 is EXP
word #27/141 is DIV
word #28/141 is SWAP3
word #29/141 is CALLVALUE
word #30/141 is SSTORE
word #31/141 is CALLDATALOAD
word #32/141 is CALLER
word #33/141 is RETURN
word #34/141 is DUP5
word #35/141 is NOT
word #36/141 is LT
word #37/141 is DUP6
word #38/141 is INVALID
word #39/141 is PUSH32
word #40/141 is STOP
word #41/141 is PUSH3
word #42/141 is GT
word #43/141 is OR
word #44/141 is DUP7
word #45/141 is DUP8
word #46/1

In [88]:
embed_vector_len = reloaded_word_vectors["CALLDATACOPY"].shape[0]
vocab_len = len(reloaded_word_vectors.index_to_key)
emb_matrix = np.zeros((vocab_len, embed_vector_len))

In [89]:
for index, word in enumerate(reloaded_word_vectors.index_to_key):
  embedding_vector = reloaded_word_vectors[word]
  if embedding_vector is not None:
    emb_matrix[index, :] = embedding_vector

In [90]:
emb_matrix

array([[-1.98992324,  0.60704881, -1.51110828, ..., -0.09835938,
         0.00501041, -0.09191697],
       [-1.89084136,  0.04977977, -2.19321203, ...,  0.96601826,
         0.52566642, -0.34974027],
       [-2.13094163,  2.25112343, -2.4615159 , ...,  0.30947116,
        -0.50818515, -0.45590296],
       ...,
       [ 1.41815913, -0.00356629,  1.23468506, ..., -0.53606832,
        -0.66652673,  0.40787336],
       [ 1.68465686, -0.22327398,  1.44521689, ..., -0.6117332 ,
        -0.39531705,  0.38962615],
       [ 1.50451946, -0.07061207,  1.01416194, ..., -0.52020484,
        -0.58324385,  0.42276809]])

In [91]:
embedding_layer = tf.keras.layers.Embedding(input_dim=vocab_len, output_dim=embed_vector_len, input_length=maxLen, weights = [emb_matrix], trainable=False)

In [117]:
reloaded_word_vectors.key_to_index 

{'HEX': 0,
 'PUSH1': 1,
 'SWAP1': 2,
 'POP': 3,
 'DUP1': 4,
 'PUSH2': 5,
 'DUP2': 6,
 'ADD': 7,
 'JUMPDEST': 8,
 'AND': 9,
 'ISZERO': 10,
 'PUSH20': 11,
 'MSTORE': 12,
 'SWAP2': 13,
 'JUMPI': 14,
 'MLOAD': 15,
 'JUMP': 16,
 'DUP3': 17,
 'SLOAD': 18,
 'SUB': 19,
 'DUP4': 20,
 'REVERT': 21,
 'PUSH4': 22,
 'EQ': 23,
 'KECCAK256': 24,
 'MUL': 25,
 'EXP': 26,
 'DIV': 27,
 'SWAP3': 28,
 'CALLVALUE': 29,
 'SSTORE': 30,
 'CALLDATALOAD': 31,
 'CALLER': 32,
 'RETURN': 33,
 'DUP5': 34,
 'NOT': 35,
 'LT': 36,
 'DUP6': 37,
 'INVALID': 38,
 'PUSH32': 39,
 'STOP': 40,
 'PUSH3': 41,
 'GT': 42,
 'OR': 43,
 'DUP7': 44,
 'DUP8': 45,
 'CALLDATASIZE': 46,
 'SWAP4': 47,
 'PUSH29': 48,
 'LOG3': 49,
 'DUP9': 50,
 'SHA3': 51,
 'LOG1': 52,
 'CALL': 53,
 'EXTCODESIZE': 54,
 'GAS': 55,
 'CODECOPY': 56,
 'PUSH6': 57,
 'RETURNDATASIZE': 58,
 'PUSH8': 59,
 'ADDRESS': 60,
 'DUP10': 61,
 'TIMESTAMP': 62,
 'SWAP5': 63,
 'PUSH5': 64,
 'CALLDATACOPY': 65,
 'DUP11': 66,
 'LOG2': 67,
 'SWAP6': 68,
 'DUP12': 69,
 'RETURNDAT

In [93]:
def adjust_hex(row):
    array = row.opcode.split()
    result_string = ""
    for i in range(len(array)):
        if("0x" in array[i]):
            array[i] = "HEX"
        result_string  = result_string + array[i] + " "
    return result_string

data["opcode_adjusted"] = data.apply(lambda row:adjust_hex(row),axis = 1)
data

opcode       vulnerability  \
0    PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x32 PUSH1 ...  Overflow-Underflow   
1    PUSH1 0x55 PUSH1 0x23 PUSH1 0xB DUP3 DUP3 DUP3...  Overflow-Underflow   
2    PUSH1 0x80 PUSH1 0x40 MSTORE CALLVALUE DUP1 IS...  Overflow-Underflow   
3    PUSH1 0x80 PUSH1 0x40 MSTORE CALLVALUE DUP1 IS...  Overflow-Underflow   
4    PUSH1 0x4C PUSH1 0x2C PUSH1 0xB DUP3 DUP3 DUP3...  Overflow-Underflow   
..                                                 ...                 ...   
744  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 PUSH1 0...                 TOD   
745  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 DUP1 PU...                 TOD   
746  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 DUP1 PU...                 TOD   
747  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 PUSH1 0...                 TOD   
748  PUSH1 0x80 PUSH1 0x40 MSTORE PUSH1 0x0 DUP1 PU...                 TOD   

                                       opcode_adjusted  
0    PUSH1 HEX PUSH1 HEX MSTORE PUSH1 HEX PUSH1 HEX...  
1    PUSH1 HEX PUSH1 HEX PUSH1 HEX DUP3 DUP3 DUP3 C...  
2    PUSH1 HEX PUSH1 HEX MSTORE CALLVALUE DUP1 ISZE...  
3    PUSH1 HEX PUSH1 HEX MSTORE CALLVALUE DUP1 ISZE...  
4    PUSH1 HEX PUSH1 HEX PUSH1 HEX DUP3 DUP3 DUP3 C...  
..                                                 ...  
744  PUSH1 HEX PUSH1 HEX MSTORE PUSH1 HEX PUSH1 HEX...  
745  PUSH1 HEX PUSH1 HEX MSTORE PUSH1 HEX DUP1 PUSH...  
746  PUSH1 HEX PUSH1 HEX MSTORE PUSH1 HEX DUP1 PUSH...  
747  PUSH1 HEX PUSH1 HEX MSTORE PUSH1 HEX PUSH1 HEX...  
748  PUSH1 HEX PUSH1 HEX MSTORE PUSH1 HEX DUP1 PUSH...  

[749 rows x 3 columns]

In [94]:
reviews = data["opcode_adjusted"]

reviews_list = []
for i in range(len(reviews)):
  reviews_list.append(reviews[i])


In [95]:
sentiment = data['vulnerability']

In [96]:
unique_labels = np.unique(sentiment)
label_numbers = np.searchsorted(unique_labels, sentiment)
label_numbers


array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,

In [97]:

X_train, X_test,Y_train, Y_test = train_test_split(reviews_list, label_numbers, test_size=0.2, random_state = 45)
     

In [98]:
tokenizer = tf.keras.preprocessing.text.Tokenizer()
tokenizer.fit_on_texts(X_train)

In [99]:
tokenizer

In [100]:
words_to_index = tokenizer.word_index
words_to_index

{'hex': 1,
 'push1': 2,
 'pop': 3,
 'dup1': 4,
 'swap1': 5,
 'push2': 6,
 'dup2': 7,
 'jumpdest': 8,
 'add': 9,
 'iszero': 10,
 'and': 11,
 'jumpi': 12,
 'push20': 13,
 'mstore': 14,
 'jump': 15,
 'mload': 16,
 'swap2': 17,
 'revert': 18,
 'sub': 19,
 'dup3': 20,
 'dup4': 21,
 'sload': 22,
 'eq': 23,
 'push4': 24,
 'mul': 25,
 'swap3': 26,
 'exp': 27,
 'keccak256': 28,
 'calldataload': 29,
 'lt': 30,
 'caller': 31,
 'dup9': 32,
 'callvalue': 33,
 'sstore': 34,
 'returndatasize': 35,
 'stop': 36,
 'div': 37,
 'dup6': 38,
 'calldatasize': 39,
 'dup5': 40,
 'swap4': 41,
 'not': 42,
 'call': 43,
 'gt': 44,
 'return': 45,
 'or': 46,
 'push3': 47,
 'returndatacopy': 48,
 'push32': 49,
 'invalid': 50,
 'push8': 51,
 'timestamp': 52,
 'dup7': 53,
 'dup8': 54,
 'address': 55,
 'origin': 56,
 'push5': 57,
 'codecopy': 58,
 'log3': 59,
 'balance': 60,
 'log1': 61,
 'gas': 62,
 'dup10': 63,
 'push6': 64,
 'calldatacopy': 65,
 'shl': 66,
 'extcodesize': 67,
 'push29': 68,
 'shr': 69,
 'dup12': 70,


In [101]:
len(words_to_index)


141

In [102]:
def imdb_rating(input_shape):

  X_indices = Input(input_shape)

  embeddings = embedding_layer(X_indices)

  X = LSTM(128, return_sequences=True)(embeddings)

  X = Dropout(0.6)(X)

  X = LSTM(128, return_sequences=True)(X)

  X = Dropout(0.6)(X)

  X = LSTM(128)(X)

  X = Dense(1, activation='sigmoid')(X)

  model = Model(inputs=X_indices, outputs=X)

  return model

In [103]:
def conv1d_model(input_shape):

  X_indices = Input(input_shape)

  embeddings = embedding_layer(X_indices)

  X = Conv1D(512,3,activation='relu')(embeddings)
  
  X = MaxPooling1D(3)(X)

  X = Conv1D(256,3,activation='relu')(X)
  
  X = MaxPooling1D(3)(X)

  X = Conv1D(256,3,activation='relu')(X)
  X = Dropout(0.8)(X)
  X = MaxPooling1D(3)(X)

  X = GlobalMaxPooling1D()(X)

  X = Dense(256, activation='relu')(X)
  X = Dense(1, activation='sigmoid')(X)

  model = Model(inputs=X_indices, outputs=X)

  return model

In [104]:
model = imdb_rating((maxLen,))
model.summary()
     

2022-12-06 22:28:19.755446: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2022-12-06 22:28:19.756144: W tensorflow/compiler/xla/stream_executor/cuda/cuda_driver.cc:265] failed call to cuInit: UNKNOWN ERROR (303)
2022-12-06 22:28:19.756476: I tensorflow/compiler/xla/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (DESKTOP-02M5AEU): /proc/driver/nvidia/version does not exist
2022-12-06 22:28:19.761490: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, None)]            0         
                                                                 
 embedding_3 (Embedding)     (None, None, 100)         14100     
                                                                 
 lstm (LSTM)                 (None, None, 128)         117248    
                                                                 
 dropout (Dropout)           (None, None, 128)         0         
                                                                 
 lstm_1 (LSTM)               (None, None, 128)         131584    
                                                                 
 dropout_1 (Dropout)         (None, None, 128)         0         
                                                                 
 lstm_2 (LSTM)               (None, 128)               131584

In [105]:
model_1d = conv1d_model((maxLen,))
model_1d.summary()

Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(None, None)]            0         
                                                                 
 embedding_3 (Embedding)     (None, None, 100)         14100     
                                                                 
 conv1d (Conv1D)             (None, None, 512)         154112    
                                                                 
 max_pooling1d (MaxPooling1D  (None, None, 512)        0         
 )                                                               
                                                                 
 conv1d_1 (Conv1D)           (None, None, 256)         393472    
                                                                 
 max_pooling1d_1 (MaxPooling  (None, None, 256)        0         
 1D)                                                       

In [107]:
X_train_indices = tokenizer.texts_to_sequences(X_train)
X_train_indices

[[2,
  1,
  2,
  1,
  2,
  1,
  20,
  20,
  20,
  58,
  4,
  16,
  2,
  1,
  75,
  2,
  1,
  23,
  2,
  1,
  12,
  50,
  8,
  55,
  2,
  1,
  14,
  2,
  1,
  7,
  74,
  20,
  7,
  45,
  50,
  13,
  1,
  55,
  23,
  2,
  1,
  2,
  1,
  14,
  2,
  1,
  4,
  18,
  50,
  71,
  64,
  1,
  28,
  1,
  16,
  33,
  1,
  69,
  105,
  1,
  1,
  109,
  1,
  1,
  1,
  62,
  135,
  1,
  136,
  113,
  1],
 [2,
  1,
  2,
  1,
  14,
  33,
  4,
  10,
  47,
  1,
  12,
  2,
  1,
  4,
  18,
  8,
  3,
  2,
  1,
  16,
  47,
  1,
  84,
  19,
  4,
  47,
  1,
  21,
  58,
  7,
  9,
  4,
  2,
  1,
  14,
  7,
  9,
  5,
  4,
  4,
  16,
  5,
  2,
  1,
  9,
  5,
  26,
  17,
  5,
  4,
  16,
  5,
  2,
  1,
  9,
  5,
  26,
  17,
  5,
  4,
  16,
  20,
  9,
  26,
  17,
  5,
  2,
  1,
  9,
  4,
  16,
  20,
  9,
  26,
  17,
  5,
  2,
  1,
  9,
  4,
  16,
  5,
  2,
  1,
  9,
  5,
  26,
  17,
  5,
  3,
  3,
  3,
  31,
  2,
  1,
  4,
  6,
  1,
  27,
  7,
  22,
  7,
  13,
  1,
  25,
  42,
  11,
  5,
  21,
  13,
  1,
  11,
  25,

In [108]:
X_train_indices = pad_sequences(X_train_indices, maxlen=maxLen, padding='post')
X_train_indices.shape

(599, 29527)

In [114]:
adam = tf.keras.optimizers.Adam(learning_rate = 0.0001)
model.compile(optimizer=adam, loss='binary_crossentropy', metrics=['accuracy'])

In [120]:
model.debug = True

model.fit(X_train_indices, Y_train, batch_size=64, epochs=15)


Epoch 1/15


InvalidArgumentError: Graph execution error:

Detected at node 'model/embedding_3/embedding_lookup' defined at (most recent call last):
    File "/home/demirbey05/ENTER/lib/python3.9/runpy.py", line 197, in _run_module_as_main
      return _run_code(code, main_globals, None,
    File "/home/demirbey05/ENTER/lib/python3.9/runpy.py", line 87, in _run_code
      exec(code, run_globals)
    File "/home/demirbey05/ENTER/lib/python3.9/site-packages/ipykernel_launcher.py", line 17, in <module>
      app.launch_new_instance()
    File "/home/demirbey05/ENTER/lib/python3.9/site-packages/traitlets/config/application.py", line 846, in launch_instance
      app.start()
    File "/home/demirbey05/ENTER/lib/python3.9/site-packages/ipykernel/kernelapp.py", line 712, in start
      self.io_loop.start()
    File "/home/demirbey05/ENTER/lib/python3.9/site-packages/tornado/platform/asyncio.py", line 199, in start
      self.asyncio_loop.run_forever()
    File "/home/demirbey05/ENTER/lib/python3.9/asyncio

In [125]:
for i in reloaded_word_vectors.key_to_index.keys():
    if (i.lower() not in words_to_index.keys()):
        print(i)

SHA3


In [122]:
words_to_index.keys()

dict_keys(['hex', 'push1', 'pop', 'dup1', 'swap1', 'push2', 'dup2', 'jumpdest', 'add', 'iszero', 'and', 'jumpi', 'push20', 'mstore', 'jump', 'mload', 'swap2', 'revert', 'sub', 'dup3', 'dup4', 'sload', 'eq', 'push4', 'mul', 'swap3', 'exp', 'keccak256', 'calldataload', 'lt', 'caller', 'dup9', 'callvalue', 'sstore', 'returndatasize', 'stop', 'div', 'dup6', 'calldatasize', 'dup5', 'swap4', 'not', 'call', 'gt', 'return', 'or', 'push3', 'returndatacopy', 'push32', 'invalid', 'push8', 'timestamp', 'dup7', 'dup8', 'address', 'origin', 'push5', 'codecopy', 'log3', 'balance', 'log1', 'gas', 'dup10', 'push6', 'calldatacopy', 'shl', 'extcodesize', 'push29', 'shr', 'dup12', 'log2', 'dup11', 'mod', 'mstore8', 'byte', 'swap10', 'swap6', 'staticcall', 'push9', 'swap5', 'dup13', 'dup14', 'number', 'codesize', 'dup15', 'sdiv', 'signextend', 'gasprice', 'push19', 'push7', 'swap8', 'push16', 'gaslimit', 'push21', 'push15', 'push13', 'swap7', 'push31', 'push27', 'swap9', 'swap12', 'selfdestruct', 'mulmod',